In [1]:
# pip install duckdb
# !pip install h3
# !pip install folium mapclassify
# !pip install --upgrade geopandas

In [1]:
import geopandas as gpd
import pandas as pd
import numpy as np

import duckdb
import h3

from shapely.geometry import Polygon

import folium

In [3]:
# Cria conexão com o banco de dados
db = duckdb.connect('../data/dbase.db')

In [4]:
# Lista as tabelas do banco de dados
db.sql("SHOW TABLES")

┌────────────────────────┐
│          name          │
│        varchar         │
├────────────────────────┤
│ RegiaoRisco_geo        │
│ RegiaoRisco_h3_cell_11 │
│ RegiaoRisco_h3_cell_12 │
│ RegiaoRisco_h3_cell_13 │
│ RegiaoRisco_h3_cell_14 │
│ RegiaoRisco_h3_cell_15 │
│ RegiaoRisco_h3_cell_16 │
│ RegiaoRisco_h3_cell_17 │
│ RegiaoRisco_h3_cell_21 │
│ RegiaoRisco_h3_cell_22 │
│           ·            │
│           ·            │
│           ·            │
│ RegiaoRisco_h3_cell_33 │
│ RegiaoRisco_h3_cell_35 │
│ RegiaoRisco_h3_cell_41 │
│ RegiaoRisco_h3_cell_42 │
│ RegiaoRisco_h3_cell_43 │
│ RegiaoRisco_h3_cell_50 │
│ RegiaoRisco_h3_cell_51 │
│ RegiaoRisco_h3_cell_52 │
│ RegiaoRisco_h3_cell_53 │
│ RegiaoRisco_h3_geo_28  │
├────────────────────────┤
│   28 rows (20 shown)   │
└────────────────────────┘

In [5]:
# Instala as extensões para geometria e H3
db.sql("""
        INSTALL spatial;
        INSTALL h3 FROM community;
        LOAD spatial;
        LOAD h3;
       """)

In [7]:
# Cria tabela com os dados de RegiaoRisco
db.sql(
    """
    drop table if exists RegiaoRisco_geo;
    create table RegiaoRisco_geo as
    select cd_RegiaoRisco
            ,case when count(*) over (partition by substr(cd_RegiaoRisco,1,7)) > 1 then 2 else 1 end as tp_RegiaoRisco
            ,substr(cd_RegiaoRisco,1,2) as cd_UF
            ,geometry
    from '../data/gdf_novos_por_regiao.parquet'
    """
)

In [ ]:
# RASCUNHO QUE DEU CERTO
q = '''
with original as (
select
    cd_RegiaoRisco,
    tp_RegiaoRisco,
    cd_UF,
    geometry,
    st_astext(geometry) as wkt
from RegiaoRisco_geo
where cd_UF = '28'
),


dump as (
select
    cd_RegiaoRisco,
    tp_RegiaoRisco,
    unnest(st_dump(geometry)).geom as geometry
from original
),


cells as (
select
    cd_RegiaoRisco,
    st_asText(geometry) as wkt,
    h3_polygon_wkt_to_cells(st_asText(geometry), 8) as h3_cells

from dump
where tp_RegiaoRisco = 1

union all


select
    cd_RegiaoRisco,
    st_asText(geometry) as wkt,
    h3_polygon_wkt_to_cells(st_asText(geometry), 10) as h3_cells

from dump
where tp_RegiaoRisco = 2

),



compact as (
select 
    cd_RegiaoRisco
    ,h3_cells
    ,h3_compact_cells(h3_cells) as h3_cells_compact

from cells
),



cpct_cells as (
select 
    cd_RegiaoRisco,
    unnest([ST_GeomFromText(h3_cell_to_boundary_wkt(cell)) for cell in h3_cells_compact]) as geometry

from compact
),




coverage1 as (
select 
    cd_RegiaoRisco,
    count(*) as n_cover1,
    st_astext(st_union_agg(geometry)) as cover1_wkt
from cpct_cells
group by 1
),




exterior as (
select 
    cd_RegiaoRisco,
    st_astext(st_union_agg(ST_MakePolygon(st_exteriorring(geometry)))) as exterior_wkt
from (
    select 
        cd_RegiaoRisco,
        unnest(st_dump(st_geomfromtext(cover1_wkt))).geom as geometry
    from coverage1
)
group by 1
)


select 
    o.cd_RegiaoRisco,
    o.tp_RegiaoRisco,
    o.cd_UF,
    o.wkt,
    c1.n_cover1,
    c1.cover1_wkt,
    e.exterior_wkt as exterior_wkt
    
from original o
left join coverage1 c1
on o.cd_RegiaoRisco = c1.cd_RegiaoRisco
left join exterior e
on o.cd_RegiaoRisco = e.cd_RegiaoRisco


            
'''


# db.sql(q)

teste = db.sql(q).to_df()

In [48]:
# Cria tabela com de-para RegiaoRisco - H3Cell (nível 8 e 10)
# uf = '28'

def salvar_celulas_h3(uf):
    q = f'''
    drop table if exists RegiaoRisco_h3_cell_{uf};

    create table RegiaoRisco_h3_cell_{uf} as

    with original as (
    select
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        geometry
    from RegiaoRisco_geo
    where cd_UF = {uf}
    ),


    dump as (
    select
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        unnest(st_dump(geometry)).geom as geometry
    from original
    ),


    cells as (
    select
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        h3_polygon_wkt_to_cells(st_asText(geometry), 8) as h3_cells

    from dump
    where tp_RegiaoRisco = 1

    union all


    select
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        h3_polygon_wkt_to_cells(st_asText(geometry), 10) as h3_cells

    from dump
    where tp_RegiaoRisco = 2

    ),



    compact as (
    select 
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        h3_cells,
        h3_compact_cells(h3_cells) as h3_cells_compact

    from cells
    ),



    cpct_cells as (
    select 
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        unnest(h3_cells_compact) as h3_cell

    from compact
    )

    select 
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        h3_cell
    from cpct_cells
    '''



    db.sql(q)

    print(uf, '- ', db.sql(f"select count(*) as n from RegiaoRisco_h3_cell_{uf}").to_df().n[0], 'celulas h3 salvas')






# REVISAR
def criar_geometria_h3(uf):
    # print('combinando geometrias para criar a geometria...')
    # print('')

    q=f'''
    drop table if exists RegiaoRisco_h3_geo_{uf};

    create table RegiaoRisco_h3_geo_{uf} as

    with cells as (
    select 
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        ST_GeomFromText(h3_cell_to_boundary_wkt(h3_cell)) as geometry
    from RegiaoRisco_h3_cell_{uf}
    ),


    coverage1 as (
    select 
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        st_union_agg(geometry) as cover1
    from cells
    group by 1,2,3
    ),
     
    exterior as (
    select 
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        st_union_agg(ST_MakePolygon(st_exteriorring(geometry))) as geometry
    from (
        select 
            cd_RegiaoRisco,
            tp_RegiaoRisco,
            cd_UF,
            unnest(st_dump(cover1)).geom as geometry
        from coverage1
        )
    group by 1,2,3
    )

    select 
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        geometry
        
    from exterior
    '''


    db.sql(q)

    print(uf, '- ', db.sql(f"select count(*) as n from RegiaoRisco_h3_geo_{uf}").to_df().n[0], 'regioes h3 salvas')


# 53m 23s

In [ ]:
# for uf in ['28', '21', '22', '23', '24', '25', '26', '27', 
#            '11', '12', '13', '14', '15', '16', '17', 
#            '31', '32', '33', '35', '41', '42', '43', 
#            '50', '51', '52', '53']:
#     print(uf, '- ', db.sql(f"select count(*) as n from RegiaoRisco_h3_cell_{uf}").to_df().n[0])

28 -  7014
21 -  29096
22 -  286077
23 -  168389
24 -  60270
25 -  64534
26 -  112141
27 -  31630
11 -  323853
12 -  201184
13 -  2039491
14 -  307607
15 -  1499911
16 -  171314
17 -  324147
31 -  715118
32 -  57756
33 -  54943
35 -  314476
41 -  276203
42 -  138510
43 -  429141
50 -  476719
51 -  1156772
52 -  418860
53 -  342328


In [ ]:
# CRIA AS TABELAS COM AS CELULAS H3 POR UF
for uf in ['28', '29', '21', '22', '23', '24', '25', '26', '27', 
           '11', '12', '13', '14', '15', '16', '17', 
           '31', '32', '33', '35', '41', '42', '43', 
           '50', '51', '52', '53']:
    salvar_celulas_h3(uf)

28 -  7014 celulas h3 salvas
29 -  56602 celulas h3 salvas
21 -  29096 celulas h3 salvas
22 -  17967 celulas h3 salvas
23 -  24607 celulas h3 salvas
24 -  10315 celulas h3 salvas
25 -  12407 celulas h3 salvas
26 -  20623 celulas h3 salvas
27 -  9192 celulas h3 salvas
11 -  19689 celulas h3 salvas
12 -  6862 celulas h3 salvas
13 -  27893 celulas h3 salvas
14 -  6317 celulas h3 salvas
15 -  45277 celulas h3 salvas
16 -  4214 celulas h3 salvas
17 -  19659 celulas h3 salvas
31 -  130902 celulas h3 salvas
32 -  11010 celulas h3 salvas
33 -  40116 celulas h3 salvas
35 -  172013 celulas h3 salvas
41 -  72646 celulas h3 salvas
42 -  41284 celulas h3 salvas
43 -  71067 celulas h3 salvas
50 -  44969 celulas h3 salvas
51 -  52778 celulas h3 salvas
52 -  54441 celulas h3 salvas
53 -  19678 celulas h3 salvas


In [24]:
# PRINTA NUMERO DE REGIOES POR UF
print('total - ', db.sql(f"select count(*) as n from RegiaoRisco_geo").to_df().n[0], 'regioes')

for uf in ['28', '21', '22', '23', '24', '25', '26', '27', '29',
           '11', '12', '13', '14', '15', '16', '17', 
           '31', '32', '33', '35', '41', '42', '43', 
           '50', '51', '52', '53']:
    print(uf, '- ', db.sql(f"select count(*) as n from RegiaoRisco_geo where cd_UF = {uf}").to_df().n[0], 'regioes')

total -  2170 regioes
28 -  22 regioes
21 -  25 regioes
22 -  14 regioes
23 -  76 regioes
24 -  30 regioes
25 -  35 regioes
26 -  84 regioes
27 -  26 regioes
29 -  96 regioes
11 -  12 regioes
12 -  2 regioes
13 -  8 regioes
14 -  1 regioes
15 -  21 regioes
16 -  1 regioes
17 -  10 regioes
31 -  287 regioes
32 -  35 regioes
33 -  175 regioes
35 -  606 regioes
41 -  166 regioes
42 -  92 regioes
43 -  154 regioes
50 -  36 regioes
51 -  27 regioes
52 -  108 regioes
53 -  21 regioes


In [49]:
# CRIA AS TABELAS COM AS GEOMETRIAS H3 POR UF
for uf in ['28', '21', '22', '23', '24', '25', '26', '27', '29',
           '11', '12', '13', '14', '15', '16', '17', 
           '31', '32', '33', '35', '41', '42', '43', 
           '50', '51', '52', '53']:
        
    criar_geometria_h3(uf)

28 -  22 regioes h3 salvas
21 -  25 regioes h3 salvas
22 -  14 regioes h3 salvas
23 -  76 regioes h3 salvas
24 -  30 regioes h3 salvas
25 -  35 regioes h3 salvas
26 -  84 regioes h3 salvas
27 -  26 regioes h3 salvas
29 -  96 regioes h3 salvas
11 -  12 regioes h3 salvas
12 -  2 regioes h3 salvas
13 -  8 regioes h3 salvas
14 -  1 regioes h3 salvas
15 -  21 regioes h3 salvas
16 -  1 regioes h3 salvas
17 -  10 regioes h3 salvas
31 -  287 regioes h3 salvas
32 -  35 regioes h3 salvas
33 -  175 regioes h3 salvas
35 -  606 regioes h3 salvas
41 -  166 regioes h3 salvas
42 -  92 regioes h3 salvas
43 -  154 regioes h3 salvas
50 -  36 regioes h3 salvas
51 -  27 regioes h3 salvas
52 -  108 regioes h3 salvas
53 -  21 regioes h3 salvas


In [53]:
# CRIA TABELA COM TODAS AS REGIOES H3 E AJUSTA AS REGIOES QUE SE SOBREPOEM
db.sql(
'''
drop table if exists RegiaoRisco_h3_geo;

create table RegiaoRisco_h3_geo as

select *
from RegiaoRisco_h3_geo_21

union all

select *
from RegiaoRisco_h3_geo_22

union all

select *
from RegiaoRisco_h3_geo_23

union all

select *
from RegiaoRisco_h3_geo_24

union all

select *
from RegiaoRisco_h3_geo_25

union all

select *
from RegiaoRisco_h3_geo_26

union all

select *
from RegiaoRisco_h3_geo_27

union all

select *
from RegiaoRisco_h3_geo_28

union all

select *
from RegiaoRisco_h3_geo_29

union all

select *
from RegiaoRisco_h3_geo_11

union all

select *
from RegiaoRisco_h3_geo_12

union all

select
    cd_RegiaoRisco
    ,tp_RegiaoRisco
    ,cd_UF
    ,case 
        when cd_RegiaoRisco = '130004' then 
            st_difference(geometry, (select st_union_agg(geometry) from RegiaoRisco_h3_geo_13 where substr(cd_RegiaoRisco,1,7)= '1302603')) 
        else 
            geometry
    end as geometry
from RegiaoRisco_h3_geo_13

union all

select *
from RegiaoRisco_h3_geo_14

union all

select *
from RegiaoRisco_h3_geo_15

union all

select *
from RegiaoRisco_h3_geo_16

union all

select *
from RegiaoRisco_h3_geo_17

union all

select  
    cd_RegiaoRisco
    ,tp_RegiaoRisco
    ,cd_UF
    ,case 
        when cd_RegiaoRisco = '3114105' then 
            st_difference(geometry, (select geometry from RegiaoRisco_h3_geo_31 where cd_RegiaoRisco= '3163706')) 
        when cd_RegiaoRisco = '3148004' then 
            st_difference(geometry, (select geometry from RegiaoRisco_h3_geo_31 where cd_RegiaoRisco= '3137502'))
        else 
            geometry
    end as geometry

from RegiaoRisco_h3_geo_31

union all

select *
from RegiaoRisco_h3_geo_32

union all

select *
from RegiaoRisco_h3_geo_33

union all

select
    cd_RegiaoRisco
    ,tp_RegiaoRisco
    ,cd_UF
    ,case 
        when cd_RegiaoRisco = '3534708' then 
            st_difference(geometry, (select geometry from RegiaoRisco_h3_geo_35 where cd_RegiaoRisco= '3529005'))
        when cd_RegiaoRisco = '350009' then 
            st_difference(geometry, (select st_union_agg(geometry) from RegiaoRisco_h3_geo_35 where substr(cd_RegiaoRisco,1,7)= '3506003')) 
        else 
            geometry
    end as geometry

from RegiaoRisco_h3_geo_35

union all

select *
from RegiaoRisco_h3_geo_41

union all

select *
from RegiaoRisco_h3_geo_42

union all

select *
from RegiaoRisco_h3_geo_43

union all

select *
from RegiaoRisco_h3_geo_50

union all

select *
from RegiaoRisco_h3_geo_51

union all

select *
from RegiaoRisco_h3_geo_52

union all

select *
from RegiaoRisco_h3_geo_53
'''
)

In [123]:
df = db.sql("select cd_RegiaoRisco, tp_RegiaoRisco, cd_UF, st_astext(geometry) as wkt from RegiaoRisco_h3_geo ").to_df()

In [124]:
df = gpd.GeoDataFrame(df, geometry = gpd.GeoSeries.from_wkt(df.wkt)) 

In [128]:
m = folium.Map(tiles = 'cartodb positron')
m = df.explore(m=m, color='blue', tooltip='cd_RegiaoRisco')
# m = cover1.explore(m=m, color='green', tooltip='cd_RegiaoRisco')
# m = exteriors.explore(m=m, color='red', tooltip='cd_RegiaoRisco')
# m = cover2.explore(m=m, color='red')
folium.LayerControl().add_to(m)

m.save('full.html')
# m  

In [129]:
# SALVA BASE NO PARQUET
db.sql(f"copy ({q}) to 'RegiaoRisco_h3_geo.parquet'" )

In [130]:
db.close()

## OLD

In [ ]:
db.sql('''
        select cd_RegiaoRisco 
            ,count(*) as n_celulas
        from RegiaoRisco_h3_cell_29
        group by 1
       ''')

celulas h3 salvas


In [ ]:
db.sql('''
       select 
            cd_RegiaoRisco, 
            st_union_agg(ST_GeomFromText(h3_cell_to_boundary_wkt(hex_cell)))  as geometry
       from RegiaoRisco_h3_cell_28 
       where cd_RegiaoRisco = '280005'
       group by 1
       ''')

# '2803302' = 2795  cells = 21s
# '280005' = 4373 cells = 55s

┌────────────────┬──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────

In [ ]:
db.sql('''
        with base_hex_cell as (
        select 
            cd_RegiaoRisco, 
            unnest(h3_compact_cells(h3_polygon_wkt_to_cells(st_asText(geometry), 8))) as h3_cell
        from RegiaoRisco_geo
        where cd_RegiaoRisco = '2806008'
       )

        select
            cd_RegiaoRisco,
            st_union_agg(ST_GeomFromText(h3_cell_to_boundary_wkt(h3_cell)))  as geometry
        from base_hex_cell
        group by 1
       ''')

In [6]:
teste_compact = db.sql('''
        with base_hex_cell as (
        select 
            cd_RegiaoRisco, 
            unnest(h3_compact_cells(h3_polygon_wkt_to_cells(st_asText(geometry), 8))) as h3_cell
        from RegiaoRisco_geo
        where cd_RegiaoRisco = '2806008'
       )

        select
            cd_RegiaoRisco,
            st_astext(st_union_agg(ST_GeomFromText(h3_cell_to_boundary_wkt(h3_cell))))  as wkt
        from base_hex_cell
        group by 1
       ''').to_df()

In [7]:
teste_compact = gpd.GeoDataFrame(teste_compact, geometry=gpd.GeoSeries.from_wkt(teste_compact.wkt))

In [93]:
q = '''
with original as (
select
    cd_RegiaoRisco,
    tp_RegiaoRisco,
    cd_UF,
    geometry,
    st_astext(geometry) as wkt
from RegiaoRisco_geo
where cd_UF = '28'
),


dump as (
select
    cd_RegiaoRisco,
    tp_RegiaoRisco,
    unnest(st_dump(geometry)).geom as geometry
from original
),


cells as (
select
    cd_RegiaoRisco,
    st_asText(geometry) as wkt,
    h3_polygon_wkt_to_cells(st_asText(geometry), 8) as h3_cells

from dump
where tp_RegiaoRisco = 1

union all


select
    cd_RegiaoRisco,
    st_asText(geometry) as wkt,
    h3_polygon_wkt_to_cells(st_asText(geometry), 10) as h3_cells

from dump
where tp_RegiaoRisco = 2

),



compact as (
select 
    cd_RegiaoRisco
    ,h3_cells
    ,h3_compact_cells(h3_cells) as h3_cells_compact

from cells
),



cpct_cells as (
select 
    cd_RegiaoRisco,
    unnest([ST_GeomFromText(h3_cell_to_boundary_wkt(cell)) for cell in h3_cells_compact]) as geometry

from compact
),


coverage1 as (
select 
    cd_RegiaoRisco,
    count(*) as n_cover1,
    st_astext(st_union_agg(geometry)) as cover1_wkt
from cpct_cells
group by 1
),




exterior as (
select 
    cd_RegiaoRisco,
    st_astext(st_union_agg(ST_MakePolygon(st_exteriorring(geometry)))) as exterior_wkt
from (
    select 
        cd_RegiaoRisco,
        unnest(st_dump(st_geomfromtext(cover1_wkt))).geom as geometry
    from coverage1
)
group by 1
)


select 
    o.cd_RegiaoRisco,
    o.tp_RegiaoRisco,
    o.cd_UF,
    o.wkt,
    c1.n_cover1,
    c1.cover1_wkt,
    e.exterior_wkt as exterior_wkt
    
from original o
left join coverage1 c1
on o.cd_RegiaoRisco = c1.cd_RegiaoRisco
left join exterior e
on o.cd_RegiaoRisco = e.cd_RegiaoRisco


            
'''


# db.sql(q)

teste = db.sql(q).to_df()

In [32]:
# TESTE COM COBERTURAS MISTURANDO COMPACTIFICACAO E RECOLOCANDO FILHOS DAS CELULAS MAIORES

# teste = db.sql ('''
#         with original as (
#         select
#             cd_RegiaoRisco,
#             st_asText(geometry) as wkt,
#             h3_polygon_wkt_to_cells(st_asText(geometry), 8) as h3_cells8
        
#         from RegiaoRisco_geo
#         where cd_RegiaoRisco = '2806008'
#         ),

#         compact as (
#         select 
#             cd_RegiaoRisco
#             ,h3_cells8
#             ,h3_compact_cells(h3_cells8) as h3_cells8_compact
        
#         from original
#         ),

#         children as (
#         select 
#             cd_RegiaoRisco,
#             h3_cells8,
#             h3_cells8_compact,
#             [cell for cell in h3_cells8_compact if h3_get_resolution(cell) = 8] as h3_cells8_compact_flt8,
#             flatten([h3_cell_to_children(cell,h3_get_resolution(cell)+1) for cell in h3_cells8_compact if h3_get_resolution(cell) < 8]) as children
#         from compact
#         ),
        
#         coverage as (
#         select 
#             cd_RegiaoRisco,
#             len(h3_cells8) as n_original,
#             len(h3_cells8_compact) as n_compact,
#             len(h3_cells8_compact_flt8) as n_compact_flt8,
#             len(children) as n_CHILDREN,
        
#             len(h3_cells8_compact || children),
#             len(h3_cells8_compact_flt8 || children),
        
#             h3_cells8_compact || children as cover1,
#             h3_cells8_compact_flt8 || children as cover2

#         from children
#         ),

#         coverage1 as (
#         select 
#             c1.cd_RegiaoRisco,
#             count(*) as n_cover1,
#             st_astext(st_union_agg(c1.geometry)) as cover1_wkt
        
#         from (
#                 select 
#                     cd_RegiaoRisco,
#                     unnest([ST_GeomFromText(h3_cell_to_boundary_wkt(cell)) for cell in cover1]) as geometry
#                 from coverage
#             )   c1
#         group by 1
#         ),

#         coverage2 as (
#         select 
#             c1.cd_RegiaoRisco,
#             count(*) as n_cover2,
#             st_astext(st_union_agg(c1.geometry)) as cover2_wkt
        
#         from (
#                 select 
#                     cd_RegiaoRisco,
#                     unnest([ST_GeomFromText(h3_cell_to_boundary_wkt(cell)) for cell in cover2]) as geometry
#                 from coverage
#             )   c1
#         group by 1
#         )

#         select 
#             o.cd_RegiaoRisco,
#             o.wkt,
#             c1.n_cover1,
#             c1.cover1_wkt,
#             c2.n_cover2,
#             c2.cover2_wkt
#         from original o
#         join coverage1 c1
#         on o.cd_RegiaoRisco = c1.cd_RegiaoRisco
#         join coverage2 c2
#         on o.cd_RegiaoRisco = c2.cd_RegiaoRisco
        

                    
#        ''').to_df()

In [94]:
original = gpd.GeoDataFrame(teste, geometry=gpd.GeoSeries.from_wkt(teste.wkt))
cover1 = gpd.GeoDataFrame(teste, geometry=gpd.GeoSeries.from_wkt(teste.cover1_wkt))
exteriors = gpd.GeoDataFrame(teste, geometry=gpd.GeoSeries.from_wkt(teste.exterior_wkt))
# cover2 = gpd.GeoDataFrame(teste, geometry=gpd.GeoSeries.from_wkt(teste.cover2_wkt))

In [95]:
teste

cd_RegiaoRisco  tp_RegiaoRisco cd_UF  \
0         4201208               1    42   
1         4204202               1    42   
2         4207304               1    42   
3         4213203               1    42   
4         4202008               1    42   
..            ...             ...   ...   
87   420910201002               2    42   
88   420910201000               2    42   
89   420910201001               2    42   
90        4213500               1    42   
91        4219507               1    42   

                                                  wkt  n_cover1  \
0   POLYGON ((-48.974821994 -28.0789168119999, -48...       686   
1   POLYGON ((-52.787084138 -27.205694267, -52.790...       802   
2   MULTIPOLYGON (((-48.649906471 -28.325265163, -...       257   
3   POLYGON ((-49.1233856119999 -26.682565261, -49...       118   
4   MULTIPOLYGON (((-48.627327 -27.013505021, -48....        45   
..                                                ...       ...   
87  POLYGON ((-48.8626982082984 -26.30586863883265...       152   
88  POLYGON ((-48.85482064827064 -26.3051055752670...       102   
89  POLYGON ((-48.84569733833344 -26.2934533708396...        61   
90  MULTIPOLYGON (((-48.468897134 -27.205988099, -...        88   
91  POLYGON ((-52.312599226 -26.8693401419999, -52...       170   

                                           cover1_wkt  \
0   POLYGON ((-49.305786 -27.584076, -49.300758 -2...   
1   MULTIPOLYGON (((-52.208784 -27.184826, -52.203...   
2   MULTIPOLYGON (((-48.741701 -27.808091, -48.745...   
3   POLYGON ((-49.1255 -26.803761, -49.129663 -26....   
4   POLYGON ((-48.624921 -26.969269, -48.624053 -2...   
..                                                ...   
87  POLYGON ((-48.847201 -26.282177, -48.847919 -2...   
88  POLYGON ((-48.849389 -26.295117, -48.848795 -2...   
89  MULTIPOLYGON (((-48.847919 -26.28192, -48.8458...   
90  MULTIPOLYGON (((-48.460676 -27.208843, -48.464...   
91  POLYGON ((-52.315491936755535 -26.870927960945...   

                                         exterior_wkt  
0   POLYGON ((-49.305786 -27.584076, -49.300758 -2...  
1   MULTIPOLYGON (((-52.203017 -27.191125, -52.198...  
2   MULTIPOLYGON (((-48.745008 -27.815102, -48.739...  
3   POLYGON ((-49.1255 -26.803761, -49.129663 -26....  
4   POLYGON ((-48.624921 -26.969269, -48.624053 -2...  
..                                                ...  
87  POLYGON ((-48.847201 -26.282177, -48.847919 -2...  
88  POLYGON ((-48.849389 -26.295117, -48.848795 -2...  
89  MULTIPOLYGON (((-48.845888 -26.28205, -48.8449...  
90  MULTIPOLYGON (((-48.470763 -27.205303, -48.466...  
91  POLYGON ((-52.315491936755535 -26.870927960945...  

[92 rows x 7 columns]

In [97]:
m = folium.Map(tiles = 'cartodb positron')
m = original.explore(m=m, color='blue', tooltip='cd_RegiaoRisco')
# m = cover1.explore(m=m, color='green', tooltip='cd_RegiaoRisco')
# m = exteriors.explore(m=m, color='red', tooltip='cd_RegiaoRisco')
# m = cover2.explore(m=m, color='red')
folium.LayerControl().add_to(m)

m.save('../data/original_sc.html')

In [57]:
357 - 99

258

In [58]:
2169 - 258

1911

In [12]:
teste_full = gpd.GeoDataFrame(teste_full, geometry=gpd.GeoSeries.from_wkt(teste_full.wkt))

In [17]:
original = db.sql("select cd_RegiaoRisco, tp_RegiaoRisco,  cd_UF, st_astext(geometry) as geometry from RegiaoRisco_geo where cd_RegiaoRisco = '2806008'").to_df()
original = gpd.GeoDataFrame(original, geometry=gpd.GeoSeries.from_wkt(original.geometry))


In [39]:
m = folium.Map(tiles = 'cartodb positron')
m = original.explore(m=m, color='green')
m = teste_full.explore(m=m, color='red')
m = teste_compact.explore(m=m, color='blue')

m
# 2803302
# m = teste.head(1).explore(m=m, tiles = 'cartodb positron', tooltip = 'cd_RegiaoRisco')
# m.save('mapa-original.html')

In [21]:
help(h3.compact_cells)

Help on function compact_cells in module h3.api.basic_str:

compact_cells(cells)
    Compact a collection of H3 cells by combining
    smaller cells into larger cells, if all child cells
    are present. Input cells must all share the same resolution.
    
    Parameters
    ----------
    cells : iterable of H3 Cells
    
    Returns
    -------
    unordered collection of H3Cell
    
    Notes
    -----
    There is currently no guaranteed order of the output cells.



In [82]:
# criar_geometrias_com_h3_8('28')


celulas h3 salvas
combinando geometrias para criar a geometria...



In [73]:
# db.sql(''' 
#        select distinct  a.cd_RegiaoRisco
#        from RegiaoRisco_geo a
#        left join (select distinct cd_RegiaoRisco from RegiaoRisco_h3_cell) b
#          on a.cd_RegiaoRisco = b.cd_RegiaoRisco
#        where b.cd_RegiaoRisco is null
#        order by 1 desc
#        ''')

In [74]:
# db.sql('''
#        select cd_UF, count(*)
#        from RegiaoRisco_h3_cell
#          group by 1
#        order by 2
#        ''')

In [75]:
# Cria a geometria unindo os hexagonos - apenas DF
# for uf in ['53', '52', '51', '50', '43', '42', '41', '35', '33', '32', '31',
#        '29', '27', '26', '25', '24', '23', '22', '21', '17', '15',
#        '14', '13', '12', '11']:

for uf in ['28']:
    print(uf)
    q=f"""
    drop table if exists RegiaoRisco_h3_geo_{uf};

    create table RegiaoRisco_h3_geo_{uf} as

    with base_hex_cell as (
    select
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        hex_cell,
        ST_GeomFromText(h3_cell_to_boundary_wkt(hex_cell)) as hex_geo
    from RegiaoRisco_h3_cell_{uf}
    )

    select
        cd_RegiaoRisco,
        tp_RegiaoRisco,
        cd_UF,
        st_astext(st_union_agg(hex_geo)) as geometry
    from base_hex_cell
    group by 1,2,3

    """

    db.sql(q)

28


In [ ]:
# # Cria a geometria unindo os hexagonos outras UFs
# for uf in ['52', '51', '50', '43', '42', '41', '35', '33', '32', '31',
#        '29', '53', '27', '26', '25', '24', '23', '22', '21', '17', '15',
#        '14', '13', '12', '11']:
# # for uf in ['53']:
#     print(uf)
#     q=f"""
#     drop table if exists RegiaoRisco_h3_geo_{uf};

#     create table RegiaoRisco_h3_geo_{uf} as

#     with base_hex_cell as (
#     select
#         cd_RegiaoRisco,
#         tp_RegiaoRisco,
#         cd_UF,
#         hex_cell,
#         ST_GeomFromText(h3_cell_to_boundary_wkt(hex_cell)) as hex_geo
#     from RegiaoRisco_h3_cell
#     where cd_UF = '{uf}'
#     )

#     select
#         cd_RegiaoRisco,
#         tp_RegiaoRisco,
#         cd_UF,
#         st_astext(st_union_agg(hex_geo)) as geometry
#     from base_hex_cell
#     group by 1,2,3

#     """

#     db.sql(q)

In [30]:
# db.sql("""
#        select distinct cd_RegiaoRisco  from RegiaoRisco_h3_cell_28 where cd_UF = '28'  order by 1
#        """)

┌────────────────┐
│ cd_RegiaoRisco │
│    varchar     │
├────────────────┤
│ 280005         │
│ 2800308000     │
│ 2800308003     │
│ 2800308010     │
│ 2800308012     │
│ 2800308013     │
│ 2800308022     │
│ 280030803      │
│ 2800308300     │
│ 2800308301     │
│ 280030831      │
│ 280030832      │
│ 2801009        │
│ 2801306        │
│ 2802106        │
│ 2802908        │
│ 2803005        │
│ 2803609        │
│ 2804508        │
│ 2805703        │
│ 2806008        │
├────────────────┤
│    21 rows     │
└────────────────┘

In [65]:
# db.sql("""
#        select
#               cd_RegiaoRisco
#               -- ,tp_RegiaoRisco
#               -- ,cd_UF
#               -- ,geometry1
#               -- ,unnest(h3_polygon_wkt_to_cells(st_asText(geometry1), 8)) as hex_cell
       
#        from (
#               select *,
#               unnest(st_dump(geometry)).geom  as geometry1
#               from RegiaoRisco_geo 
#               where cd_UF = '28'
#        ) a

#        """)


┌────────────────┐
│ cd_RegiaoRisco │
│    varchar     │
├────────────────┤
│ 280005         │
│ 2800308000     │
│ 2800308003     │
│ 2800308010     │
│ 2800308012     │
│ 2800308013     │
│ 2800308022     │
│ 280030803      │
│ 2800308300     │
│ 2800308301     │
│ 280030831      │
│ 280030832      │
│ 2801009        │
│ 2801306        │
│ 2802106        │
│ 2802908        │
│ 2803005        │
│ 2803302        │
│ 2803609        │
│ 2804508        │
│ 2805703        │
│ 2806008        │
├────────────────┤
│    22 rows     │
└────────────────┘

In [76]:
hex = db.sql('select * from RegiaoRisco_h3_geo_28').to_df()
original = db.sql("select cd_RegiaoRisco, tp_RegiaoRisco,  cd_UF, st_astext(geometry) as geometry from RegiaoRisco_geo where cd_UF = '28'").to_df()

hex = gpd.GeoDataFrame(hex, geometry=gpd.GeoSeries.from_wkt(hex['geometry']))
original = gpd.GeoDataFrame(original, geometry=gpd.GeoSeries.from_wkt(original['geometry']))

In [77]:
m = folium.Map(tiles = 'cartodb positron')
m = original.explore(m=m)
m = hex.explore(m=m, color='red')

m
# 2803302
# m = teste.head(1).explore(m=m, tiles = 'cartodb positron', tooltip = 'cd_RegiaoRisco')
# m.save('mapa-original.html')

In [ ]:
# teste = gpd.GeoDataFrame(teste, geometry= gpd.GeoSeries.from_wkt(teste['geometry']))

In [21]:
# teste.explore(m = folium.Map(tiles='cartodbpositron'))

In [59]:
db.sql('select count(*) from RegiaoRisco_h3_cell ')

┌──────────────┐
│ count_star() │
│    int64     │
├──────────────┤
│     13825299 │
└──────────────┘

In [64]:
db.sql("select count(*) from RegiaoRisco_h3_cell where cd_RegiaoRisco = '3525102'")

┌──────────────┐
│ count_star() │
│    int64     │
├──────────────┤
│          654 │
└──────────────┘

In [33]:
q="""
with sample as (
    select
        cd_RegiaoRisco
        
    from RegiaoRisco_geo
    where cd_UF = '35'  
        and tp_RegiaoRisco = 1
    limit 10
)

select 
    b.cd_RegiaoRisco,
    b.tp_RegiaoRisco,
    b.cd_UF,
    st_asText(st_union_agg(hex_geom)) as hex_geom_agg

from sample a 
inner join RegiaoRisco_h3_cell b
    on a.cd_RegiaoRisco = b.cd_RegiaoRisco
group by 1,2,3
"""

db.sql(q)

┌────────────────┬────────────────┬─────────┬───────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────

In [20]:
# q="""
# select
#     cd_RegiaoRisco,
#     tp_RegiaoRisco,
#     st_asText(geometry) as wkt,
#     (unnest(h3_polygon_wkt_to_cells_string(st_asText(geometry), 10))) as hex10
# from Geo_RegiaoRisco
# where cd_RegiaoRisco = '3503307'
# """





# q="""
# with base_hex_cell as (
#     select
#         cd_RegiaoRisco,
#         tp_RegiaoRisco,
#         unnest(h3_polygon_wkt_to_cells(st_asText(geometry), 8)) as hex_cell
#     from Geo_RegiaoRisco
# ),

# base_hex_geo as (
#     select
#         cd_RegiaoRisco,
#         tp_RegiaoRisco,
#         hex_cell,
#         ST_GeomFromText(h3_cell_to_boundary_wkt(hex_cell)) as hex_geom
#     from base_hex_cell
# ),

# base_hex_geo1 as (
#     select
#         cd_RegiaoRisco,
#         tp_RegiaoRisco,
#         st_asText(st_union_agg(hex_geom)) as hex_geom
#     from base_hex_geo
#     group by 1,2
# )

# -- select count(*)
# -- from base_hex_cell

# select
#     a.cd_RegiaoRisco,
#     a.tp_RegiaoRisco,
#     st_asText(a.geometry) as geom_original,
#     b.hex_geom

# from Geo_RegiaoRisco a
# inner join base_hex_geo1 b
#     on a.cd_RegiaoRisco = b.cd_RegiaoRisco

# """


# # db.sql(q)

In [43]:
q="""
select 
    cd_RegiaoRisco,
    tp_RegiaoRisco,
    cd_UF,
    st_asText(geometry) as wkt
from RegiaoRisco_geo
where cd_RegiaoRisco in ('350029', '3525102', '3526209', '350021', '3507803', '3506102',
       '3525300', '3523107', '3526100', '3529401')
"""

db.sql(q)

┌────────────────┬────────────────┬─────────┬───────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────

In [34]:
teste = db.sql(q).to_df()

In [37]:
# original = gpd.GeoDataFrame(teste, geometry=gpd.GeoSeries.from_wkt( teste['geom_original']))
hex = gpd.GeoDataFrame(teste, geometry=gpd.GeoSeries.from_wkt( teste['hex_geom_agg']))

In [46]:
teste = db.sql(q).to_df()
original = gpd.GeoDataFrame(teste, geometry=gpd.GeoSeries.from_wkt( teste['wkt']))

In [48]:
# hex
original

cd_RegiaoRisco  tp_RegiaoRisco cd_UF  \
0         350021               1    35   
1         350029               1    35   
2        3506102               1    35   
3        3507803               1    35   
4        3523107               1    35   
5        3525102               1    35   
6        3525300               1    35   
7        3526100               1    35   
8        3526209               1    35   
9        3529401               1    35   

                                                 wkt  \
0  POLYGON ((-51.969227314 -22.1945278869999, -51...   
1  POLYGON ((-50.39264875 -20.568543894, -50.3931...   
2  POLYGON ((-48.377899057 -20.917195385, -48.377...   
3  POLYGON ((-47.688441 -21.0150439989999, -47.68...   
4  POLYGON ((-46.281365663 -23.4800020169999, -46...   
5  POLYGON ((-47.778568 -21.061755999, -47.779193...   
6  POLYGON ((-48.66173464 -22.6900220649999, -48....   
7  POLYGON ((-47.8265179319999 -24.4058657849999,...   
8  POLYGON ((-47.064807759 -24.0183440879999, -47...   
9  POLYGON ((-46.4431870823926 -23.6968209484686,...   

                                            geometry  
0  POLYGON ((-51.96923 -22.19453, -51.97179 -22.1...  
1  POLYGON ((-50.39265 -20.56854, -50.39317 -20.5...  
2  POLYGON ((-48.3779 -20.9172, -48.37792 -20.917...  
3  POLYGON ((-47.68844 -21.01504, -47.68833 -21.0...  
4  POLYGON ((-46.28137 -23.48, -46.28128 -23.4804...  
5  POLYGON ((-47.77857 -21.06176, -47.77919 -21.0...  
6  POLYGON ((-48.66173 -22.69002, -48.66373 -22.6...  
7  POLYGON ((-47.82652 -24.40587, -47.82737 -24.4...  
8  POLYGON ((-47.06481 -24.01834, -47.06486 -24.0...  
9  POLYGON ((-46.44319 -23.69682, -46.44345 -23.6...

In [49]:
m = folium.Map(tiles = 'cartodb positron')
m = original.explore(m=m)
m = hex.explore(m=m, color='red')

m

# m = teste.head(1).explore(m=m, tiles = 'cartodb positron', tooltip = 'cd_RegiaoRisco')

# m.save('mapa-original.html')

In [108]:
# m

In [109]:
teste = gpd.GeoDataFrame(teste, geometry=gpd.GeoSeries(teste['hex10'].apply(lambda x: cell_to_shapely(x))))

# teste.set_geometry('h3_geom', inplace=True)

In [110]:
m = folium.Map(tiles = 'cartodb positron')
m = teste[['geometry']].dissolve().explore(m=m, color='red', tiles = 'cartodb positron')
m.save('mapa_hex10.html')
# m